In [27]:
import pandas as pd
import numpy as np
from requests import get
import json
import matplotlib.pyplot as plt

import plotly.express as px
import plotly.io as pio
pio.renderers.default = "notebook_connected"

## Import Prosecution Data

In [28]:
prosecution = pd.read_csv('./data/prosecution_all_years.csv')
prosecution.head()

Agency Name  Total Hate Crime Cases Referred  \
0     Alameda                              167   
1      Alpine                                0   
2      Amador                                5   
3       Butte                               61   
4   Calaveras                                4   

   Total Cases Filed as Hate Crimes  \
0                               116   
1                                 0   
2                                 5   
3                                34   
4                                 4   

   Total Cases Filed as Non-Bias Motivated Crimes  Total Dispositions  \
0                                               2                  86   
1                                               0                   0   
2                                               0                   4   
3                                              19                  21   
4                                               0                   4   

   Not Convicted  Total Convictions  Total Hate Crime Convictions  \
0             11                 75                            24   
1              0                  0                             0   
2              0                  4                             2   
3              2                 19                            10   
4              1                  3                             0   

   Guilty plea/Nolo contendere  Trial Verdict  All Other Convictions  
0                           24              0                     51  
1                            0              0                      0  
2                            2              0                      2  
3                            9              1                      9  
4                            0              0                      3

### Create prosecution rate column

In [29]:
prosecution['prosecution-rate'] = prosecution['Total Dispositions'] / prosecution['Total Hate Crime Cases Referred']

## Add FIPS codes to prosecution data by county

In [30]:
fips = pd.read_csv('https://raw.githubusercontent.com/kjhealy/fips-codes/master/state_and_county_fips_master.csv', dtype={'fips': str})
fips = fips[fips['state'] == 'CA']
fips['name'] = fips['name'].str.replace(' County', '')
fips['name'] = fips['name'].str.replace(' ', '')
fips.drop(columns='state', inplace=True)

In [31]:
prosecution_fips = prosecution.merge(fips, left_on='Agency Name', right_on='name').drop(columns='name').dropna()
prosecution_fips['fips'] = prosecution_fips['fips'].astype(str)
prosecution_fips['fips'] = '0' + prosecution_fips['fips']
prosecution_fips.head()

Agency Name  Total Hate Crime Cases Referred  \
0      Alameda                              167   
2       Amador                                5   
3        Butte                               61   
4    Calaveras                                4   
6  ContraCosta                               85   

   Total Cases Filed as Hate Crimes  \
0                               116   
2                                 5   
3                                34   
4                                 4   
6                                80   

   Total Cases Filed as Non-Bias Motivated Crimes  Total Dispositions  \
0                                               2                  86   
2                                               0                   4   
3                                              19                  21   
4                                               0                   4   
6                                              12                  75   

   Not Convicted  Total Convictions  Total Hate Crime Convictions  \
0             11                 75                            24   
2              0                  4                             2   
3              2                 19                            10   
4              1                  3                             0   
6             25                 50                            15   

   Guilty plea/Nolo contendere  Trial Verdict  All Other Convictions  \
0                           24              0                     51   
2                            2              0                      2   
3                            9              1                      9   
4                            0              0                      3   
6                           14              1                     35   

   prosecution-rate   fips  
0          0.514970  06001  
2          0.800000  06005  
3          0.344262  06007  
4          1.000000  06009  
6          0.882353  06013

## Plot Prosecution Rates by county in California

In [32]:
# With help from https://stackoverflow.com/questions/70950535/plot-single-state-choropleth-map-in-plotly-how-to-index-geojson
r = get(
    "https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json"
)
counties = json.loads(r.text)
target_states = ["06"]
counties["features"] = [
    f for f in counties["features"] if f["properties"]["STATE"] in target_states
]

fig = px.choropleth(
    prosecution_fips,
    geojson=counties,
    locations="fips",
    color="prosecution-rate",
    color_continuous_scale="Viridis",
    range_color=(0, 1),
    scope="usa",
    labels={"prosecution-rate": "Prosecution Rate"},
    fitbounds="geojson",
)
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
fig.show()
fig.write_image("./figures/california-prosecution-rates.png")


## Get demographics data

In [33]:
demo = pd.read_csv('./demographics-data/prosecution_all_years_demographics.csv')
demo.columns

Index(['Agency Name', 'Total Hate Crime Cases Referred',
       'Total Cases Filed as Hate Crimes',
       'Total Cases Filed as Non-Bias Motivated Crimes', 'Total Dispositions',
       'Not Convicted', 'Total Convictions', 'Total Hate Crime Convictions',
       'Guilty plea/Nolo contendere', 'Trial Verdict', 'All Other Convictions',
       'County', 'population', 'pct_Asian', 'pct_AAPI', 'pct_Black',
       'pct_Hispanic', 'pct_Multi-Racial/Ethnic',
       'pct_Hawaiian/ Pacific Island', 'pct_White', 'pct_unemployed_2018',
       'pct_u18_poverty_2017', 'median_hh_income_2017'],
      dtype='object')

## Add FIPS codes to prosecution demographic data by county

In [34]:
fips = pd.read_csv('https://raw.githubusercontent.com/kjhealy/fips-codes/master/state_and_county_fips_master.csv', dtype={'fips': str})
fips = fips[fips['state'] == 'CA']
fips['name'] = fips['name'].str.replace(' County', '')
fips['name'] = fips['name'].str.replace(' ', '')
fips.drop(columns='state', inplace=True)

In [35]:
demo_fips = demo.merge(fips, left_on='Agency Name', right_on='name').drop(columns='name').dropna()
demo_fips['fips'] = demo_fips['fips'].astype(str)
demo_fips['fips'] = '0' + demo_fips['fips']
demo_fips.head()

Agency Name  Total Hate Crime Cases Referred  \
0     Alameda                              167   
1      Alpine                                0   
2      Amador                                5   
3       Butte                               61   
4   Calaveras                                4   

   Total Cases Filed as Hate Crimes  \
0                               116   
1                                 0   
2                                 5   
3                                34   
4                                 4   

   Total Cases Filed as Non-Bias Motivated Crimes  Total Dispositions  \
0                                               2                  86   
1                                               0                   0   
2                                               0                   4   
3                                              19                  21   
4                                               0                   4   

   Not Convicted  Total Convictions  Total Hate Crime Convictions  \
0             11                 75                            24   
1              0                  0                             0   
2              0                  4                             2   
3              2                 19                            10   
4              1                  3                             0   

   Guilty plea/Nolo contendere  Trial Verdict  ...  pct_AAPI pct_Black  \
0                           24              0  ...  0.274130  0.115603   
1                            0              0  ...  0.005164  0.000861   
2                            2              0  ...  0.013527  0.026740   
3                            9              1  ...  0.046872  0.016188   
4                            0              0  ...  0.014629  0.008223   

   pct_Hispanic  pct_Multi-Racial/Ethnic  pct_Hawaiian/ Pacific Island  \
0      0.234718                 0.041847                      0.008167   
1      0.073150                 0.018933                      0.000000   
2      0.138690                 0.026662                      0.001671   
3      0.158293                 0.038862                      0.002093   
4      0.113350                 0.029257                      0.001574   

   pct_White  pct_unemployed_2018  pct_u18_poverty_2017  \
0   0.337067                0.030                 0.105   
1   0.714286                0.046                 0.353   
2   0.778242                0.040                 0.157   
3   0.736261                0.049                 0.226   
4   0.814438                0.040                 0.211   

   median_hh_income_2017   fips  
0                95550.0  06001  
1                55755.0  06003  
2                60588.0  06005  
3                48634.0  06007  
4                58536.0  06009  

[5 rows x 24 columns]

## Plot demographic Rates by county in California

In [36]:
cols = {
    "population": 'Population',
    "pct_Asian": 'Percentage Asian',
    "pct_AAPI": 'Percentage AAPI',
    "pct_Black": 'Percentage Black',
    "pct_Hispanic": 'Percentage Hispanic',
    "pct_Multi-Racial/Ethnic": 'Percentage Multi Racial',
    "pct_Hawaiian/ Pacific Island": 'Percentage Hawaiian, Pacific Islander',
    "pct_White": 'Percentage White',
    "pct_unemployed_2018": 'Percentage Unemployed in 2018',
    "pct_u18_poverty_2017": 'Percentage Under 18 Poverty',
    "median_hh_income_2017": 'Median Household Income 2017',
}


In [37]:
# With help from https://stackoverflow.com/questions/70950535/plot-single-state-choropleth-map-in-plotly-how-to-index-geojson
for col, val in cols.items():
    fig = px.choropleth(
        demo_fips,
        geojson=counties,
        locations="fips",
        color=col,
        color_continuous_scale="Viridis",
        #range_color=(0, 1),
        scope="usa",
        labels={col: val},
        fitbounds="geojson",
    )
    fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
    fig.show()
    fig.write_image(f"./figures/california-{col.replace('/','-')}.png")


## Get Hate Crimes data

In [43]:
hc = pd.read_csv('./data/hc_vis.csv', index_col=0)
hc.columns

Index(['ClosedYear', 'MonthOccurrence', 'County', 'NCIC',
       'TotalNumberOfVictims', 'TotalNumberOfIndividualVictims',
       'SuspectsRaceAsAGroup', 'TotalNumberOfSuspects', 'MostSeriousUcr',
       'MostSeriousUcrType', 'MostSeriousLocation', 'MostSeriousBias',
       'MostSeriousBiasType', 'MostSeriousVictimType', 'WeaponType',
       'Offensive_Act', 'Agency Name', 'labels'],
      dtype='object')

## Add FIPS codes to hate crime demographic data by county

In [44]:
fips = pd.read_csv('https://raw.githubusercontent.com/kjhealy/fips-codes/master/state_and_county_fips_master.csv', dtype={'fips': str})
fips = fips[fips['state'] == 'CA']
fips['name'] = fips['name'].str.replace(' County', '')
fips['name'] = fips['name'].str.replace(' ', '')
fips.drop(columns='state', inplace=True)

In [45]:
hc_fips = hc.merge(fips, left_on='County', right_on='name').drop(columns='name').dropna()
hc_fips['fips'] = hc_fips['fips'].astype(str)
hc_fips['fips'] = '0' + hc_fips['fips']
hc_fips.head()

ClosedYear  MonthOccurrence   County                              NCIC  \
0        2001                2  Alameda  Alameda Co. Sheriff's Department   
1        2001                2  Alameda  Alameda Co. Sheriff's Department   
2        2001                5  Alameda  Alameda Co. Sheriff's Department   
3        2001                9  Alameda  Alameda Co. Sheriff's Department   
4        2001                9  Alameda  Alameda Co. Sheriff's Department   

   TotalNumberOfVictims  TotalNumberOfIndividualVictims SuspectsRaceAsAGroup  \
0                     1                               1                White   
1                     2                               2                White   
2                     1                               1                White   
3                     1                               1                White   
4                     2                               2                White   

   TotalNumberOfSuspects                MostSeriousUcr MostSeriousUcrType  \
0                      2                Simple Assault     Violent Crimes   
1                      1  Destruction/Damage/Vandalism    Property Crimes   
2                      4  Destruction/Damage/Vandalism    Property Crimes   
3                      1                  Intimidation     Violent Crimes   
4                      1                  Intimidation     Violent Crimes   

       MostSeriousLocation                     MostSeriousBias  \
0           Bar/Night Club      Anti-Black or African American   
1  Residence/Home/Driveway      Anti-Black or African American   
2  Residence/Home/Driveway             Anti-Hispanic or Latino   
3  Residence/Home/Driveway             Anti-Hispanic or Latino   
4        Convenience Store  Anti-Other Race/Ethnicity/Ancestry   

       MostSeriousBiasType MostSeriousVictimType  \
0  Race/Ethnicity/Ancestry                Person   
1  Race/Ethnicity/Ancestry                Person   
2  Race/Ethnicity/Ancestry                Person   
3  Race/Ethnicity/Ancestry                Person   
4  Race/Ethnicity/Ancestry                Person   

                                    WeaponType        Offensive_Act  \
0  Personal weapons (hands, feet, teeth, etc.)         Verbal slurs   
1                                         None             Graffiti   
2                                         None  Daubing of swastika   
3                                         None         Verbal slurs   
4                                         None         Verbal slurs   

  Agency Name  labels   fips  
0     Alameda       1  06001  
1     Alameda       1  06001  
2     Alameda       1  06001  
3     Alameda       1  06001  
4     Alameda       1  06001

## Plot demographic Rates by county in California

In [46]:
# With help from https://stackoverflow.com/questions/70950535/plot-single-state-choropleth-map-in-plotly-how-to-index-geojson

fig = px.choropleth(
    hc_fips,
    geojson=counties,
    locations="fips",
    color='MostSeriousBias',
    color_continuous_scale="Viridis",
    #range_color=(0, 1),
    scope="usa",
    labels={col: val},
    fitbounds="geojson",
)
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
fig.show()
fig.write_image(f"./figures/california-{col.replace('/','-')}.png")
